In [297]:
import scipy         
import datetime
from scipy.linalg import expm
import scipy.sparse as sparse
from quspin.operators import hamiltonian, commutator, exp_op # Hamiltonians and operators
from quspin.basis import tensor_basis, spin_basis_1d # bases
import numpy as np # general math functions
import matplotlib.pyplot as plt # plotting library
from numba import jit


In [298]:
L = 7 #system size
M = 0.1 #fermion mass
N=6 #number of layers
l=1/2 #spin length
m_epsilon = 1/2
no_checks = dict(check_pcon=False,check_symm=False,check_herm=False)

In [299]:
#construct basis
basis=spin_basis_1d(L=L,S = "1/2", pauli = 0)
print(basis)

reference states: 
array index   /   Fock state   /   integer repr. 
       0.         |1 1 1 1 1 1 1>           127  
       1.         |1 1 1 1 1 1 0>           126  
       2.         |1 1 1 1 1 0 1>           125  
       3.         |1 1 1 1 1 0 0>           124  
       4.         |1 1 1 1 0 1 1>           123  
       5.         |1 1 1 1 0 1 0>           122  
       6.         |1 1 1 1 0 0 1>           121  
       7.         |1 1 1 1 0 0 0>           120  
       8.         |1 1 1 0 1 1 1>           119  
       9.         |1 1 1 0 1 1 0>           118  
      10.         |1 1 1 0 1 0 1>           117  
      11.         |1 1 1 0 1 0 0>           116  
      12.         |1 1 1 0 0 1 1>           115  
      13.         |1 1 1 0 0 1 0>           114  
      14.         |1 1 1 0 0 0 1>           113  
      15.         |1 1 1 0 0 0 0>           112  
      16.         |1 1 0 1 1 1 1>           111  
      17.         |1 1 0 1 1 1 0>           110  
      18.         |1 1 0 1 1 0 

In [300]:
#initialisation of the Gauss laws

liste = []
liste_m = []
gauss_law_map = []
Gauss_law = []
gauss_law_matrix = []
z_comp_minf = [[-m_epsilon,0]]
z_comp_pinf = [[m_epsilon,L-1]]

for i in range(L+1):
    liste.append([[1.,i]])
    liste_m.append([[-1.,i]])
    if i == 0:
        gauss_law_map.append([
            ["z",liste[0]],
            ["I",z_comp_minf],

        ])
    
    elif (i == L) & (i%2 == 0):
        gauss_law_map.append([
            ["z",liste_m[i-1]],
            ["I",z_comp_pinf],
        ])
    
    elif (i == L) & (i%2 == 1):
        gauss_law_map.append([
            ["z",liste_m[i-1]],
            ["I",liste[i-1]],
            ["I",z_comp_pinf],

        ])        
        
    elif i%2 == 0:
        gauss_law_map.append([
            ["z",liste[i]],
            ["z",liste_m[i-1]],
        ])
    elif i%2 == 1:
        gauss_law_map.append([
            ["z",liste[i]],
            ["z",liste_m[i-1]],  
            ["I",liste[i]]
        ])
    Gauss_law.append(hamiltonian(gauss_law_map[i],dynamic_list=[],basis=basis,**no_checks))
for i in range(L+1):
    gauss_law_matrix.append(Gauss_law[i].tocsc())

In [301]:
B = np.zeros((int(4*l)+1,int(4*l)+1))
for i in range(int(4*l)+1):
    for j in range(int(4*l)+1):
        B[i][j] = (-2*l+i)**j
b = np.zeros(int(4*l)+1)
b[int(2*l)+1] = 1.
solution = scipy.linalg.solve(B,b)
y = np.zeros(int(4*3/2)+1)
for i in range(int(4*l)+1):
    y[i] = solution[i]
print(y)
print(b)

[0.  0.5 0.5 0.  0.  0.  0. ]
[0. 0. 1.]


In [302]:
C = np.zeros((int(4*l)+1,int(4*l)+1))
for i in range(int(4*l)+1):
    for j in range(int(4*l)+1):
        C[i][j] = (-2*l+i+1)**j
c = np.zeros(int(4*l)+1)
c[int(2*l)] = 1.
solution = scipy.linalg.solve(C,c)
z = np.zeros(int(4*3/2)+1)
for i in range(int(4*l)+1):
    z[i] = solution[i]
print(z)
print(c)

[ 0.  2. -1.  0.  0.  0.  0.]
[0. 1. 0.]


In [303]:
#projectors on g=1 for every site
Proj = [sparse.csr_matrix((basis.Ns,basis.Ns)) for i in range(L+1)]
for i in range(int(L/2)+1):
    for j in range(int(4*l)+1):
        Proj[2*i] += y[j]*gauss_law_matrix[2*i]**j
for i in range(int(L/2)+1):
    for j in range(int(4*l)+1):
        Proj[2*i+1] += z[j]*gauss_law_matrix[2*i+1]**j

In [304]:
A = np.zeros((int(2*l)+1,int(2*l)+1), dtype = complex)
for i in range(int(2*l)+1):
    for j in range(int(2*l)+1):
        A[i][j] = (-l+i)**j
b = np.zeros(int(2*l)+1,dtype = complex)
for i in range(int(2*l)+1):
    b[i] = (-1)**(-l+i)
solution = scipy.linalg.solve(A,b)
x = np.zeros(int(2*3/2)+1, dtype = complex)
for i in range(int(2*l)+1):
    x[i] = solution[i]
print(x)
print(x.conj())

[6.123234e-17+0.j 0.000000e+00+2.j 0.000000e+00+0.j 0.000000e+00+0.j]
[6.123234e-17-0.j 0.000000e+00-2.j 0.000000e+00-0.j 0.000000e+00-0.j]


In [305]:
const_term = []
linear_term = []
quadratic_term = []
cubic_term = []

const_term_conj = []
linear_term_conj = []
quadratic_term_conj = []
cubic_term_conj = []

interaction_p = []
interaction_m = []

for i in range(L-1):
    const_term.append([[x[0]/(2*np.sqrt(l*(l+1))),i]])
    linear_term.append([[x[1]/(2*np.sqrt(l*(l+1))),i,i+1]])
    quadratic_term.append([[x[2]/(2*np.sqrt(l*(l+1))),i,i+1,i+1]])
    cubic_term.append([[(x[3])/(2*np.sqrt(l*(l+1))),i,i+1,i+1,i+1]])

    const_term_conj.append([[x.conj()[0]/(2*np.sqrt(l*(l+1))),i]])
    linear_term_conj.append([[x.conj()[1]/(2*np.sqrt(l*(l+1))),i,i+1]])
    quadratic_term_conj.append([[x.conj()[2]/(2*np.sqrt(l*(l+1))),i,i+1,i+1]])
    cubic_term_conj.append([[x.conj()[3]/(2*np.sqrt(l*(l+1))),i,i+1,i+1,i+1]])


    interaction_p.append([
        ["+", const_term[i]],
        ["+z", linear_term[i]],
        ["+zz", quadratic_term[i]],
        ["+zzz", cubic_term[i]],


    ])

    interaction_m.append([
        ["-", const_term_conj[i]],
        ["-z", linear_term_conj[i]],
        ["-zz", quadratic_term_conj[i]],
        ["-zzz", cubic_term_conj[i]],


    ])
    
const_term.append([[(0.5*(-1)**m_epsilon)/np.sqrt(l*(l+1)),L-1]])
const_term_conj.append([[(0.5*np.conj((-1)**m_epsilon))/np.sqrt(l*(l+1)),L-1]])

interaction_p.append([
    ["+", const_term[L-1]]
])
interaction_m.append([
    ["-", const_term_conj[L-1]]
])

kin_energy = [[0.5,i,i] for i in range(L)]
mass_term = [[2*(-1)**i*M,i] for i in range(L)]

kin_mass_map = [
            ["zz", kin_energy], 
            ["z", mass_term], 
]

H_int_p = []
H_int_m = []
interaction = [sparse.csr_matrix((basis.Ns,basis.Ns),dtype = complex) for i in range(L)]
h_int = sparse.csr_matrix((basis.Ns,basis.Ns))
for i in range(L):
    H_int_p.append(hamiltonian(interaction_p[i],dynamic_list=[],basis=basis,**no_checks))
    H_int_m.append(hamiltonian(interaction_m[i],dynamic_list=[],basis=basis,**no_checks))
    interaction[i] = (Proj[i]@H_int_p[i].tocsc()@Proj[i+1]+Proj[i+1]@H_int_m[i].tocsc()@Proj[i])

H_kin_mass = hamiltonian(kin_mass_map,dynamic_list=[],basis=basis,**no_checks)
h_kin_mass = H_kin_mass.tocsc()

h_int = 0

for i in range(L):
    h_int += interaction[i]


full_ham_matrix = h_kin_mass + h_int #Spin-1 Hamiltonian without the local contstaints

G=0
for i in range(L+1):
    G += 0.12*(Gauss_law[i]**2-Gauss_law[i])**2
constraint_full_matrix = G.tocsc()
constrained_full_ham_matrix= full_ham_matrix + constraint_full_matrix #Spin-1 Hamiltonian with the local contstaints as a penalty term


In [306]:
#eigenvalues and eigenvectors of the Spin-1 Hamiltonian without the local contstaints
eigenval, eigenvec = scipy.sparse.linalg.eigsh(full_ham_matrix,k = 3,which = "SA")
print(eigenval[eigenval<=1e1])
print(eigenvec[:,1])

[-0.61333138 -0.37472882 -0.37472882]
[-1.38290595e-16-5.47777100e-16j -4.86451415e-17-1.11868397e-15j
  5.30978441e-16+4.25828500e-18j -1.83860191e-01+1.03404656e-01j
 -1.99816517e-17+1.95671654e-17j  8.96938524e-17+5.02254283e-17j
 -4.68484800e-17-3.93456737e-17j  1.92854121e-17-8.35597413e-18j
  5.31495101e-16-5.04107853e-17j  9.90183673e-16-5.92127388e-17j
  6.16701200e-17+5.18062040e-16j -1.43782709e-01-2.55654992e-01j
 -9.32298170e-18-9.81723616e-18j  9.01577035e-17+3.37440512e-17j
  2.49783567e-16+1.24027414e-17j -2.18714272e-01+1.23006910e-01j
 -7.31038423e-18+1.33325854e-17j -2.29634729e-17+3.87487330e-17j
  1.62566076e-17-2.55917675e-17j  1.26919583e-18-1.10221846e-18j
  1.60200614e-17+2.16447811e-17j  1.33273096e-17-1.13429406e-17j
  7.60218193e-20-7.02215126e-18j -2.04694050e-17+3.38787395e-17j
  7.45048327e-17+2.09470912e-17j  2.02300343e-18-1.70387670e-19j
 -2.31117160e-18+5.17505757e-18j -2.71280485e-17+8.04974768e-18j
 -6.67388926e-18+7.11124768e-19j -2.49167751e-17+2.6

In [307]:
#eigenvalues and eigenvectors of the Spin-1 Hamiltonian with the local contstaints
eigenvalues, eigenvectors = scipy.sparse.linalg.eigsh(constrained_full_ham_matrix,k = 3,which = "SA")


In [343]:
#Gauge invariant part of the spectrum
string = ""
print(eigenvalues[eigenvalues<=1e1])
for i in range(basis.Ns):
    if np.abs(eigenvectors[:,0][i])>=1e-5:
        string+=str(eigenvectors[:,0][i])+basis.int_to_state(basis.Ns-i-1)+"\n"
        #for j in range(basis.Ns):
            #if (np.abs(np.abs(eigenvectors[:,0][i])-np.abs(eigenvectors[:,0][j]))<=1e-5) & (i<j):
                #print(basis.int_to_state(basis.Ns-i-1),basis.int_to_state(basis.Ns-j-1))
print(string)


[-0.61333138  0.04659467  0.10527118]
(0.32194273149035385+0.13151289622027473j)|1 1 1 1 1 1 1>
(-0.1183937797567624+0.2898272180282444j)|1 1 1 1 1 0 1>
(-0.12501370857700383+0.3060327615750197j)|1 1 1 0 1 1 1>
(-0.3129939366634457-0.12785733325750936j)|1 1 1 0 1 0 1>
(-0.06399740829821544+0.15666524750030203j)|1 1 1 0 0 0 1>
(-0.11839377975676238+0.28982721802824424j)|1 0 1 1 1 1 1>
(-0.26279757658543695-0.10735223080337143j)|1 0 1 1 1 0 1>
(-0.31299393666344594-0.1278573332575094j)|1 0 1 0 1 1 1>
(0.1329218184335342-0.32539176408586734j)|1 0 1 0 1 0 1>
(-0.1722736603496931-0.0703734105447103j)|1 0 1 0 0 0 1>
(-0.06399740829821536+0.15666524750030228j)|1 0 0 0 1 1 1>
(-0.17227366034969335-0.0703734105447102j)|1 0 0 0 1 0 1>
(-0.04543912615755752+0.11123469113779262j)|1 0 0 0 0 0 1>



In [309]:
#initial state
string = ""
for i in range(L):
    string +="0"
psi_0 = np.zeros(basis.Ns)
i_0 = basis.index(string)
psi_0[i_0] = 1.

In [310]:
#cost function of the initial state
expt_value = 0
matvec_h = full_ham_matrix@psi_0
matvec_c = constraint_full_matrix@psi_0
for i in range(basis.Ns):
    expt_value += np.conj(psi_0[i])*(matvec_h[i]+matvec_c[i])
print(np.real(expt_value))

1.7349999999999999


In [311]:
expt_value = 0
matvec = full_ham_matrix@psi_0
for i in range(basis.Ns):
    expt_value += np.conj(psi_0[i])*matvec[i]
print(expt_value)

(0.775+0j)


In [312]:
def rot_sigma(k,i,j,phi,theta):
    if k>=L:
        print("Warning! Rotations apply to k<=L-1!")
    sigma = np.zeros((int(2*l)+1,int(2*l)+1),dtype = complex)
    sigma[int(2*l)-i][int(2*l)-j] = 0.5*(np.cos(phi)+1j*np.sin(phi))
    sigma[int(2*l)-j][int(2*l)-i] = 0.5*(np.cos(phi)-1j*np.sin(phi))
    sigma = sparse.csc_matrix(sigma)
    rot_matrix = expm(-1j*theta*sigma/2)
    if k==0:
        tensprod = rot_matrix
        for i in range(L-1):
            tensprod = scipy.sparse.kron(tensprod,sparse.identity(int(2*l)+1))
    else:
        tensprod = sparse.identity(int(2*l)+1)
        for i in range(1,k):
            tensprod = scipy.sparse.kron(tensprod,sparse.identity(int(2*l)+1))
        tensprod = scipy.sparse.kron(tensprod,rot_matrix)
        for i in range(k+1,L):
            tensprod = scipy.sparse.kron(tensprod,sparse.identity(int(2*l)+1))
    return tensprod

def rot_ms(k,i,j,phi,theta):
    sigma = np.zeros((int(2*l)+1,int(2*l)+1),dtype = complex)
    sigma[int(2*l)-i][int(2*l)-j] = 0.5*(np.cos(phi)+1j*np.sin(phi))
    sigma[int(2*l)-j][int(2*l)-i] = 0.5*(np.cos(phi)-1j*np.sin(phi))
    sigma = sparse.csc_matrix(sigma)
    power_matrix = scipy.sparse.kron(sigma,sparse.identity(int(2*l)+1))+scipy.sparse.kron(sparse.identity(int(2*l)+1),sigma)
    rot_matrix = scipy.sparse.linalg.expm(-1j*power_matrix@power_matrix*theta/4)
    if k == 0:
        tensprod = rot_matrix
        for i in range(L-2):
            tensprod = scipy.sparse.kron(tensprod,sparse.identity(int(2*l)+1))
    else:
        tensprod = sparse.identity(int(2*l)+1)
        for i in range(1,k):
            tensprod = scipy.sparse.kron(tensprod,sparse.identity(int(2*l)+1))
        tensprod = scipy.sparse.kron(tensprod,rot_matrix)
        for i in range(k+2,L):
            tensprod = scipy.sparse.kron(tensprod,sparse.identity(int(2*l)+1))
    return tensprod

def rot_ms_e(i,j,phi,theta):
    ms_e = sparse.identity(basis.Ns,dtype = complex)
    for k in range(1,int(L/2)):
        ms_e = rot_ms(2*k,i,j,phi,theta)@ms_e
    return(ms_e)

def rot_ms_o(i,j,phi,theta):
    ms_o = sparse.identity(basis.Ns,dtype = complex)
    for k in range(int(L/2)-1):
        ms_o = rot_ms(2*k+1,i,j,phi,theta)@ms_o
    return(ms_o)

def rot_sigma_e(i,j,phi,theta):
    sigma_e = sparse.identity(basis.Ns,dtype = complex)
    for k in range(1,int(L/2)):
        sigma_e = rot_sigma(2*k,i,j,phi,theta)@sigma_e
    return(sigma_e)

def rot_sigma_o(i,j,phi,theta):
    sigma_o = sparse.identity(basis.Ns,dtype = complex)
    for k in range(int(L/2)):
        sigma_o = rot_sigma(2*k+1,i,j,phi,theta)@sigma_o
    return(sigma_o)

def rot_sigma_all(i,j,phi,theta):
    sigma_all = sparse.identity(basis.Ns,dtype = complex)
    for k in range(L):
        sigma_all = rot_sigma(k,i,j,phi,theta)@sigma_all
    return(sigma_all)

In [313]:

def ms_hamiltonian(i,j,phi):
    sigma = np.zeros((int(2*l+1),int(2*l+1)),dtype = complex)
    sigma[int(2*l)-i][int(2*l)-j] = 0.5*(np.cos(phi)+1j*np.sin(phi))
    sigma[int(2*l)-j][int(2*l)-i] = 0.5*(np.cos(phi)-1j*np.sin(phi))    
    sigma = sparse.csc_matrix(sigma)
    summe = np.zeros((basis.Ns,basis.Ns),dtype = complex)
    for k in range(L):
        if k == 0:
            tensprod = sigma
            for m in range(L-1):
                tensprod = scipy.sparse.kron(tensprod,sparse.identity(int(2*l+1)))
            tensprod = tensprod.toarray()
        else:
            tensprod = sparse.identity(int(2*l+1))
            for i in range(1,k):
                tensprod = scipy.sparse.kron(tensprod,sparse.identity(int(2*l+1)))
            tensprod = scipy.sparse.kron(tensprod,sigma)
            for i in range(k+1,L):
                tensprod = scipy.sparse.kron(tensprod,sparse.identity(int(2*l+1)))
            tensprod = tensprod.toarray()
        summe +=tensprod
    return summe@summe

def sigma_e_hamiltonian(i,j,phi):
    sigma = np.zeros((int(2*l+1),int(2*l+1)),dtype = complex)
    sigma[int(2*l)-i][int(2*l)-j] = 0.5*(np.cos(phi)+1j*np.sin(phi))
    sigma[int(2*l)-j][int(2*l)-i] = 0.5*(np.cos(phi)-1j*np.sin(phi))
    sigma = sparse.csc_matrix(sigma)
    summe = np.zeros((basis.Ns,basis.Ns),dtype = complex)
    for k in range(1,int(L/2)):
        if 2*k == 0:
            tensprod = sigma
            for m in range(L-1):
                tensprod = scipy.sparse.kron(tensprod,sparse.identity(int(2*l+1)))
            tensprod = tensprod.toarray()
        else:
            tensprod = sparse.identity(int(2*l+1))
            for i in range(1,2*k):
                tensprod = scipy.sparse.kron(tensprod,sparse.identity(int(2*l+1)))
            tensprod = scipy.sparse.kron(tensprod,sigma)
            for i in range(2*k+1,L):
                tensprod = scipy.sparse.kron(tensprod,sparse.identity(int(2*l+1)))
            tensprod = tensprod.toarray()
        summe +=tensprod
    return summe

def sigma_o_hamiltonian(i,j,phi):
    sigma = np.zeros((int(2*l+1),int(2*l+1)),dtype = complex)
    sigma[int(2*l)-i][int(2*l)-j] = 0.5*(np.cos(phi)+1j*np.sin(phi))
    sigma[int(2*l)-j][int(2*l)-i] = 0.5*(np.cos(phi)-1j*np.sin(phi))
    sigma = sparse.csc_matrix(sigma)
    summe = np.zeros((basis.Ns,basis.Ns),dtype = complex)
    for k in range(int(L/2)):
        tensprod = sparse.identity(int(2*l+1))
        for i in range(1,2*k+1):
            tensprod = scipy.sparse.kron(tensprod,sparse.identity(int(2*l+1)))
        tensprod = scipy.sparse.kron(tensprod,sigma)
        for i in range(2*k+2,L):
            tensprod = scipy.sparse.kron(tensprod,sparse.identity(int(2*l+1)))
        tensprod = tensprod.toarray()
        summe +=tensprod
    return summe

def sigma_z_e_hamiltonian(i,j):
    sigma = np.zeros((int(2*l+1),int(2*l+1)),dtype = complex)
    sigma[int(2*l)-i][int(2*l)-i] = 0.5
    sigma[int(2*l)-j][int(2*l)-j] = -0.5
    sigma = sparse.csc_matrix(sigma)
    summe = np.zeros((basis.Ns,basis.Ns),dtype = complex)
    for k in range(int(L/2)+1):
        if 2*k == 0:
            tensprod = sigma
            for m in range(L-1):
                tensprod = scipy.sparse.kron(tensprod,sparse.identity(int(2*l+1)))
            tensprod = tensprod.toarray()
        else:
            tensprod = sparse.identity(int(2*l+1))
            for i in range(1,2*k):
                tensprod = scipy.sparse.kron(tensprod,sparse.identity(int(2*l+1)))
            tensprod = scipy.sparse.kron(tensprod,sigma)
            for i in range(2*k+1,L):
                tensprod = scipy.sparse.kron(tensprod,sparse.identity(int(2*l+1)))
            tensprod = tensprod.toarray()
        summe +=tensprod
    return summe

def sigma_z_o_hamiltonian(i,j):
    sigma = np.zeros((int(2*l+1),int(2*l+1)),dtype = complex)
    sigma[int(2*l)-i][int(2*l)-i] = 0.5
    sigma[int(2*l)-j][int(2*l)-j] = -0.5
    sigma = sparse.csc_matrix(sigma)
    summe = np.zeros((basis.Ns,basis.Ns),dtype = complex)
    for k in range(int(L/2)):
        tensprod = sparse.identity(int(2*l+1))
        for i in range(1,2*k+1):
            tensprod = scipy.sparse.kron(tensprod,sparse.identity(int(2*l+1)))
        tensprod = scipy.sparse.kron(tensprod,sigma)
        for i in range(2*k+2,L):
            tensprod = scipy.sparse.kron(tensprod,sparse.identity(int(2*l+1)))
        tensprod = tensprod.toarray()
        summe +=tensprod
    return summe


matrix_part_ms_hamiltonian = ms_hamiltonian(0,1,0)
ms_ham_eigenval, ms_ham_eigenvec = scipy.linalg.eigh(matrix_part_ms_hamiltonian)

matrix_part_sigma_e_hamiltonian = sigma_e_hamiltonian(0,1,0)
sigma_e_ham_eigenval, sigma_e_ham_eigenvec = scipy.linalg.eigh(matrix_part_sigma_e_hamiltonian)


matrix_part_sigma_o_hamiltonian = sigma_o_hamiltonian(0,1,0)
sigma_o_ham_eigenval, sigma_o_ham_eigenvec = scipy.linalg.eigh(matrix_part_sigma_o_hamiltonian)


matrix_part_sigma_z_e_hamiltonian = sigma_z_e_hamiltonian(0,1)
sigma_z_e_ham_eigenval, sigma_z_e_ham_eigenvec = scipy.linalg.eigh(matrix_part_sigma_z_e_hamiltonian)


matrix_part_sigma_z_o_hamiltonian = sigma_z_o_hamiltonian(0,1)
sigma_z_o_ham_eigenval, sigma_z_o_ham_eigenvec = scipy.linalg.eigh(matrix_part_sigma_z_o_hamiltonian)


def ms_gate_global(theta):
    exponential = np.zeros((basis.Ns,basis.Ns),dtype = complex)
    for i in range(basis.Ns):
        exponential[i][i] = np.exp(-1j*ms_ham_eigenval[i]*theta/4)
    exponential = scipy.sparse.csc_matrix(exponential)
    return ms_ham_eigenvec@exponential@ms_ham_eigenvec.T.conj()

def sigma_e(theta):
    exponential = np.zeros((basis.Ns,basis.Ns),dtype = complex)
    for i in range(basis.Ns):
        exponential[i][i] = np.exp(-1j*sigma_e_ham_eigenval[i]*theta/2)
    exponential = scipy.sparse.csc_matrix(exponential)
    return sigma_e_ham_eigenvec@exponential@sigma_e_ham_eigenvec.T.conj()

def sigma_o(theta):
    exponential = np.zeros((basis.Ns,basis.Ns),dtype = complex)
    for i in range(basis.Ns):
        exponential[i][i] = np.exp(-1j*sigma_o_ham_eigenval[i]*theta/2)
    exponential = scipy.sparse.csc_matrix(exponential)
    return sigma_o_ham_eigenvec@exponential@sigma_o_ham_eigenvec.T.conj()

def sigma_z_e(theta):
    exponential = np.zeros((basis.Ns,basis.Ns),dtype = complex)
    for i in range(basis.Ns):
        exponential[i][i] = np.exp(-1j*sigma_z_e_ham_eigenval[i]*theta/2)
    exponential = scipy.sparse.csc_matrix(exponential)
    return sigma_z_e_ham_eigenvec@exponential@sigma_z_e_ham_eigenvec.T.conj()

def sigma_z_o(theta):
    exponential = np.zeros((basis.Ns,basis.Ns),dtype = complex)
    for i in range(basis.Ns):
        exponential[i][i] = np.exp(-1j*sigma_z_o_ham_eigenval[i]*theta/2)
    exponential = scipy.sparse.csc_matrix(exponential)
    return sigma_z_o_ham_eigenvec@exponential@sigma_z_o_ham_eigenvec.T.conj()



In [314]:
def cost_function_sigma(theta):
    psi_var = psi_0
    for i in range(N):
        psi_var = ms_gate_global(theta[3*i+0])@psi_var
        psi_var = sigma_e(theta[3*i+1])@psi_var
        psi_var = sigma_o(theta[3*i+2])@psi_var

    cost = np.conj(psi_var)@constrained_full_ham_matrix@psi_var
    return np.real(cost)

import datetime
print(datetime.datetime.now())
a = cost_function_sigma(np.pi*np.ones(3*N))
print(datetime.datetime.now())


2022-04-01 12:21:06.536133
2022-04-01 12:21:06.557601


In [315]:
opt_params = []
function_values = []
def callback_function(x,fun,context):
    opt_params.append(x)
    function_values.append(fun)


In [319]:
import optuna
theta = np.zeros(5*N)
#cost function definition
def cost_function_sigma(trial):
    psi_var = psi_0
    for i in range(N):
    
        theta[5*i+0] = trial.suggest_float("5*"+str(i)+"+0", -10*np.pi, 10*np.pi)
        theta[5*i+1] = trial.suggest_float("5*"+str(i)+"+1", -10*np.pi, 10*np.pi)
        theta[5*i+2] = trial.suggest_float("5*"+str(i)+"+2", -10*np.pi, 10*np.pi)
        theta[5*i+3] = trial.suggest_float("5*"+str(i)+"+3", -10*np.pi, 10*np.pi)
        theta[5*i+4] = trial.suggest_float("5*"+str(i)+"+4", -10*np.pi, 10*np.pi)
        
        psi_var = ms_gate_global(theta[5*i+0])@psi_var
        psi_var = sigma_z_e(theta[5*i+2])@sigma_e(theta[5*i+1])@psi_var
        psi_var = sigma_z_o(theta[5*i+4])@sigma_o(theta[5*i+3])@psi_var
    

    cost = np.conj(psi_var)@constrained_full_ham_matrix@psi_var
    return np.real(cost)

if __name__ == "__main__":
    sampler = optuna.samplers.CmaEsSampler(n_startup_trials = 100, restart_strategy = 'ipop', inc_popsize = 3)
    study = optuna.create_study(sampler=sampler)
    study.optimize(cost_function_sigma, n_trials=6000)

/home/ppopov/anaconda3/lib/python3.8/site-packages/optuna/samplers/_cmaes.py:221: ExperimentalWarning: `restart_strategy` option is an experimental feature. The interface can change in the future.
  warnings.warn(
[I 2022-04-01 12:26:38,694] A new study created in memory with name: no-name-67eeb4a0-a66a-45e0-a174-1d592269b70a
[I 2022-04-01 12:26:38,750] Trial 0 finished with value: 2.2652957429799403 and parameters: {'5*0+0': -28.936653761552048, '5*0+1': -8.31678048388057, '5*0+2': 14.581384430640838, '5*0+3': -3.758723023105272, '5*0+4': 28.1961841122476, '5*1+0': 19.656225455521387, '5*1+1': 24.88294175223743, '5*1+2': -10.11414881234418, '5*1+3': 30.134097058131957, '5*1+4': 18.03512727326501, '5*2+0': 17.408619740126618, '5*2+1': -28.674662952211836, '5*2+2': 23.50576630150794, '5*2+3': -27.615651994660837, '5*2+4': -14.841596399969308, '5*3+0': 2.6537438802639812, '5*3+1': -0.533486331562127, '5*3+2': 9.752001664575353, '5*3+3': 15.19342340136518, '5*3+4': -11.911280158872014, '5

[I 2022-04-01 12:26:39,024] Trial 8 finished with value: 2.384685327365631 and parameters: {'5*0+0': 7.814510480684639, '5*0+1': -26.71444777424991, '5*0+2': -20.898057186790457, '5*0+3': 25.494734116308877, '5*0+4': -21.581690887503125, '5*1+0': -27.311264270650454, '5*1+1': -27.44558651917998, '5*1+2': -14.057241616840518, '5*1+3': -20.84667488935083, '5*1+4': -4.11940402618378, '5*2+0': 11.086500908051867, '5*2+1': -20.074578359275748, '5*2+2': -8.79679419518866, '5*2+3': -18.202583036530463, '5*2+4': 15.536145160077659, '5*3+0': -23.404054526759925, '5*3+1': -0.6790229755574444, '5*3+2': 26.60266239436217, '5*3+3': -1.8044273776868245, '5*3+4': 23.0151478687474, '5*4+0': 16.613495053328478, '5*4+1': 17.10931035412922, '5*4+2': 21.505111332812632, '5*4+3': 15.144370173139997, '5*4+4': -18.500778572514182, '5*5+0': -6.888899049904989, '5*5+1': -7.696489979944008, '5*5+2': -5.629577485931701, '5*5+3': 24.955484408193357, '5*5+4': 14.750786426667403}. Best is trial 2 with value: 1.9002

[I 2022-04-01 12:26:39,290] Trial 16 finished with value: 1.9772150365885213 and parameters: {'5*0+0': 4.4810890752779216, '5*0+1': 27.821341095872874, '5*0+2': 19.542495588056113, '5*0+3': -0.6560671248217744, '5*0+4': 25.33371800669005, '5*1+0': 27.761027641784324, '5*1+1': 10.229294654214875, '5*1+2': -5.56540980035231, '5*1+3': 21.74253689114235, '5*1+4': -31.172992658304313, '5*2+0': 19.166366310808584, '5*2+1': -10.646270471806467, '5*2+2': 24.627139999776475, '5*2+3': -19.528668336919267, '5*2+4': 18.338015852017328, '5*3+0': -24.942813438698696, '5*3+1': -30.780419966379103, '5*3+2': 1.2260005720277434, '5*3+3': 6.274575264263284, '5*3+4': -13.24752839548611, '5*4+0': 19.074462918745382, '5*4+1': 20.21846017104359, '5*4+2': -6.399452177281219, '5*4+3': -5.60208479495066, '5*4+4': -23.148414797806858, '5*5+0': 26.601443043865906, '5*5+1': 1.1993434732916768, '5*5+2': -1.5653320704565772, '5*5+3': 10.25610029124826, '5*5+4': 24.837090472626258}. Best is trial 2 with value: 1.9002

[I 2022-04-01 12:26:39,555] Trial 24 finished with value: 2.274573752085464 and parameters: {'5*0+0': 25.875004914691516, '5*0+1': 12.458548508738026, '5*0+2': -11.959514956751839, '5*0+3': 20.712482877114518, '5*0+4': -11.626419338068711, '5*1+0': 5.515540449072688, '5*1+1': 20.621013983692052, '5*1+2': 23.340946808875465, '5*1+3': 12.03854840464549, '5*1+4': -1.9976001751974515, '5*2+0': -30.210758382384174, '5*2+1': 30.379286696754463, '5*2+2': -18.607160494372984, '5*2+3': 14.005214883963475, '5*2+4': -31.18440721228812, '5*3+0': -13.852195323163173, '5*3+1': -12.228253300228637, '5*3+2': 3.342960906237451, '5*3+3': 8.48664123156371, '5*3+4': 24.789011852869443, '5*4+0': -8.199344729015014, '5*4+1': -15.264411558351561, '5*4+2': -25.888295273793005, '5*4+3': -5.5425895199819095, '5*4+4': -23.559464282737654, '5*5+0': 18.13118955380692, '5*5+1': -26.83963917406175, '5*5+2': 28.881303799714424, '5*5+3': 10.944400620960188, '5*5+4': 20.66337531243836}. Best is trial 22 with value: 1.5

[I 2022-04-01 12:26:39,821] Trial 32 finished with value: 2.0311101792910358 and parameters: {'5*0+0': -7.139165788836916, '5*0+1': 17.155864170670604, '5*0+2': 27.510093944757664, '5*0+3': 17.056159245067136, '5*0+4': -27.823622895338698, '5*1+0': 8.372295165005333, '5*1+1': 10.19400817118106, '5*1+2': 12.473146418018253, '5*1+3': 30.882469385983285, '5*1+4': -14.7544548283057, '5*2+0': -2.5289679372752047, '5*2+1': 28.114233604706186, '5*2+2': 29.692513178551252, '5*2+3': 26.080638093327835, '5*2+4': -30.737118420060916, '5*3+0': 15.68340044582473, '5*3+1': -17.376739663912645, '5*3+2': 17.348441340018482, '5*3+3': -24.76544113691594, '5*3+4': 29.373668352760937, '5*4+0': -2.5892558796843197, '5*4+1': -7.081830234815271, '5*4+2': -26.661601045016695, '5*4+3': -4.080361623368205, '5*4+4': 1.1368562665930426, '5*5+0': -11.43051739462339, '5*5+1': 1.070692420744379, '5*5+2': -6.4228071250156376, '5*5+3': 16.53791543997628, '5*5+4': -4.09007512475803}. Best is trial 22 with value: 1.5917

...

[I 2022-04-01 12:30:01,077] Trial 5965 finished with value: 2.365503015518122 and parameters: {'5*0+0': 16.165965240700686, '5*0+1': 17.7911895074229, '5*0+2': 6.7867490955340175, '5*0+3': -22.875194399695435, '5*0+4': -4.966071716656294, '5*1+0': -17.21612174958987, '5*1+1': 26.605432456393654, '5*1+2': 5.66578071406047, '5*1+3': -0.30174986857662023, '5*1+4': 27.530009552247, '5*2+0': -13.934674770922982, '5*2+1': 20.47844125188725, '5*2+2': 7.913768387576423, '5*2+3': 14.241132434966222, '5*2+4': -26.2698887192875, '5*3+0': 3.6723694711280226, '5*3+1': -18.739682411696958, '5*3+2': -3.1789246891764322, '5*3+3': -5.751394802346217, '5*3+4': 29.894469317390048, '5*4+0': 23.84663826051616, '5*4+1': -14.575482811878821, '5*4+2': 11.85197305509888, '5*4+3': -10.207859654168024, '5*4+4': 7.163430210733629, '5*5+0': -19.56917695308159, '5*5+1': 8.096475522177839, '5*5+2': -10.085495254965092, '5*5+3': -14.933974670347618, '5*5+4': 19.717013215676875}. Best is trial 5113 with value: 0.92529

[I 2022-04-01 12:30:01,370] Trial 5973 finished with value: 2.2373625658431093 and parameters: {'5*0+0': 16.963578794987534, '5*0+1': 16.43265764998211, '5*0+2': 8.39438751437958, '5*0+3': -21.36666615665873, '5*0+4': -2.8785891785187987, '5*1+0': -17.349759949468645, '5*1+1': 24.15093242999738, '5*1+2': 6.801662163320522, '5*1+3': 4.668720804662593, '5*1+4': 27.322426929102885, '5*2+0': -11.899119338037298, '5*2+1': 17.635774384635525, '5*2+2': 10.520137367306992, '5*2+3': 15.158705572213076, '5*2+4': -31.289258266443973, '5*3+0': -2.8486463539186446, '5*3+1': -20.34137787535254, '5*3+2': -4.3779559567097355, '5*3+3': -4.034262465891107, '5*3+4': 27.114398326221824, '5*4+0': 23.470102576427642, '5*4+1': -16.65150707225623, '5*4+2': 12.147042500820966, '5*4+3': -5.916211279744602, '5*4+4': 3.6452021096185225, '5*5+0': -19.00048027654497, '5*5+1': 9.851401602867863, '5*5+2': -14.509889772329073, '5*5+3': -13.629443163304643, '5*5+4': 23.047474002101023}. Best is trial 5113 with value: 0

[I 2022-04-01 12:30:01,694] Trial 5981 finished with value: 2.051244545353655 and parameters: {'5*0+0': 13.152794519448436, '5*0+1': 18.304640088124437, '5*0+2': 5.153709621257509, '5*0+3': -21.560053275679866, '5*0+4': -0.8756332273309165, '5*1+0': -15.952006968439894, '5*1+1': 27.690123849878873, '5*1+2': 4.958665946810218, '5*1+3': -8.144577454152024, '5*1+4': 26.38918970244985, '5*2+0': -8.609154182985108, '5*2+1': 23.026362460267016, '5*2+2': 7.242824986041907, '5*2+3': 10.900002611067311, '5*2+4': -27.743001267302475, '5*3+0': -0.9898804245366091, '5*3+1': -14.711945830501744, '5*3+2': 3.535562336228569, '5*3+3': -2.395188866224267, '5*3+4': 29.853653954825297, '5*4+0': 21.890887053603667, '5*4+1': -13.639751193269255, '5*4+2': 10.457632962067047, '5*4+3': -4.767101208106239, '5*4+4': 2.0098753490299353, '5*5+0': -17.663468227088334, '5*5+1': 2.354544186555353, '5*5+2': -9.40032900201838, '5*5+3': -15.609211713063543, '5*5+4': 24.9437196762234}. Best is trial 5113 with value: 0.9

[I 2022-04-01 12:30:02,037] Trial 5989 finished with value: 2.1779097965420453 and parameters: {'5*0+0': 16.373902345129185, '5*0+1': 14.430579276147299, '5*0+2': 6.790344720513946, '5*0+3': -21.859355677002203, '5*0+4': -2.827605118909033, '5*1+0': -19.609001380835707, '5*1+1': 29.210542599525414, '5*1+2': 2.465136644094313, '5*1+3': -3.1520612470876, '5*1+4': 29.929040669644824, '5*2+0': -12.673872574662635, '5*2+1': 22.340135744767906, '5*2+2': 8.526682106207966, '5*2+3': 12.241640162966757, '5*2+4': -23.87069236569815, '5*3+0': 0.2549911894080479, '5*3+1': -17.38233345751799, '5*3+2': -0.9632313874580853, '5*3+3': -1.076271800481081, '5*3+4': 24.14657818101406, '5*4+0': 22.53677410392029, '5*4+1': -16.40813865224194, '5*4+2': 11.957725485127296, '5*4+3': -4.368856188983591, '5*4+4': 7.39802144839253, '5*5+0': -22.230970975844798, '5*5+1': 8.867515935616897, '5*5+2': -14.658749130840746, '5*5+3': -11.987807025703503, '5*5+4': 22.75452832590126}. Best is trial 5113 with value: 0.9252

[I 2022-04-01 12:30:02,369] Trial 5997 finished with value: 2.030903019453544 and parameters: {'5*0+0': 18.732805847699044, '5*0+1': 15.687484529383852, '5*0+2': 7.178002714863391, '5*0+3': -23.338265956493345, '5*0+4': -1.4820585606433798, '5*1+0': -19.934729363005395, '5*1+1': 23.822254365915054, '5*1+2': 3.697955509179187, '5*1+3': -3.6481309341362196, '5*1+4': 24.108686954596994, '5*2+0': -13.574205096131212, '5*2+1': 21.585330052307445, '5*2+2': 10.623453413813902, '5*2+3': 15.242655283712995, '5*2+4': -27.339960895464223, '5*3+0': 0.5435869654164676, '5*3+1': -15.708587963663495, '5*3+2': 1.385152395737909, '5*3+3': -3.3284562129759956, '5*3+4': 29.82574271005629, '5*4+0': 25.670621192848763, '5*4+1': -15.407124857681964, '5*4+2': 11.572924557561619, '5*4+3': -7.957792645263742, '5*4+4': 4.970804882821676, '5*5+0': -18.285417804541748, '5*5+1': 9.687390729923573, '5*5+2': -11.574930010638395, '5*5+3': -9.694155050261738, '5*5+4': 24.785401737490627}. Best is trial 5113 with value

In [320]:
theta = np.zeros(5*N)
i=0
for value in study.best_trial.params.items():
    theta[i] = value[1]
    i+=1

psi_var = psi_0
for i in range(N):

    psi_var = ms_gate_global(theta[5*i+0])@psi_var
    psi_var = sigma_z_e(theta[5*i+2])@sigma_e(theta[5*i+1])@psi_var
    psi_var = sigma_z_o(theta[5*i+4])@sigma_o(theta[5*i+3])@psi_var

    
print(np.abs(np.dot(np.conj(psi_var),eigenvectors[:,0]))**2)
print(np.real(np.conj(psi_var)@constrained_full_ham_matrix@psi_var))

0.27614027791287055
0.9252979259014485


In [ ]:
string = ""
for i in range(basis.Ns):
    if np.abs(psi_var[i])>=1e-5:
        string+=str(psi_var[i])+basis.int_to_state(basis.Ns-i-1)+"\n"
        #for j in range(basis.Ns):
            #if (np.abs(np.abs(eigenvectors[:,0][i])-np.abs(eigenvectors[:,0][j]))<=1e-5) & (i<j):
                #print(basis.int_to_state(basis.Ns-i-1),basis.int_to_state(basis.Ns-j-1))
print(string)

In [ ]:
string = ""
for i in range(basis.Ns):
    if np.abs(eigenvectors[:,0][i])>=1e-5:
        string+=str(eigenvectors[:,0][i])+basis.int_to_state(basis.Ns-i-1)+"\n"
        #for j in range(basis.Ns):
            #if (np.abs(np.abs(eigenvectors[:,0][i])-np.abs(eigenvectors[:,0][j]))<=1e-5) & (i<j):
                #print(basis.int_to_state(basis.Ns-i-1),basis.int_to_state(basis.Ns-j-1))
print(string)

In [ ]:
f = open("M=0.1,L=5.txt", "w")
f.write(Energy,"\n",Fidelity)
f.close()
